In [26]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
from catboost import CatBoostClassifier
from sklearn.model_selection import (GridSearchCV,
                                     train_test_split,
                                     StratifiedKFold)



In [19]:
data = pd.read_csv('BankChurners.csv', sep=',')

In [20]:
data

CLIENTNUM     Attrition_Flag  Customer_Age Gender  Dependent_count  \
0      768805383  Existing Customer            45      M                3   
1      818770008  Existing Customer            49      F                5   
2      713982108  Existing Customer            51      M                3   
3      769911858  Existing Customer            40      F                4   
4      709106358  Existing Customer            40      M                3   
...          ...                ...           ...    ...              ...   
10122  772366833  Existing Customer            50      M                2   
10123  710638233  Attrited Customer            41      M                2   
10124  716506083  Attrited Customer            44      F                1   
10125  717406983  Attrited Customer            30      M                2   
10126  714337233  Attrited Customer            43      F                2   

      Education_Level Marital_Status Income_Category Card_Category  \
0         High School        Married     $60K - $80K          Blue   
1            Graduate         Single  Less than $40K          Blue   
2            Graduate        Married    $80K - $120K          Blue   
3         High School        Unknown  Less than $40K          Blue   
4          Uneducated        Married     $60K - $80K          Blue   
...               ...            ...             ...           ...   
10122        Graduate         Single     $40K - $60K          Blue   
10123         Unknown       Divorced     $40K - $60K          Blue   
10124     High School        Married  Less than $40K          Blue   
10125        Graduate        Unknown     $40K - $60K          Blue   
10126        Graduate        Married  Less than $40K        Silver   

       Months_on_book  ...  Credit_Limit  Total_Revolving_Bal  \
0                  39  ...       12691.0                  777   
1                  44  ...        8256.0                  864   
2                  36  ...        3418.0                    0   
3                  34  ...        3313.0                 2517   
4                  21  ...        4716.0                    0   
...               ...  ...           ...                  ...   
10122              40  ...        4003.0                 1851   
10123              25  ...        4277.0                 2186   
10124              36  ...        5409.0                    0   
10125              36  ...        5281.0                    0   
10126              25  ...       10388.0                 1961   

       Avg_Open_To_Buy  Total_Amt_Chng_Q4_Q1  Total_Trans_Amt  Total_Trans_Ct  \
0              11914.0                 1.335             1144              42   
1               7392.0                 1.541             1291              33   
2               3418.0                 2.594             1887              20   
3                796.0                 1.405             1171              20   
4               4716.0                 2.175              816              28   
...                ...                   ...              ...             ...   
10122           2152.0                 0.703            15476             117   
10123           2091.0                 0.804             8764              69   
10124           5409.0                 0.819            10291              60   
10125           5281.0                 0.535             8395              62   
10126           8427.0                 0.703            10294              61   

       Total_Ct_Chng_Q4_Q1  Avg_Utilization_Ratio  \
0                    1.625                  0.061   
1                    3.714                  0.105   
2                    2.333                  0.000   
3                    2.333                  0.760   
4                    2.500                  0.000   
...                    ...                    ...   
10122                0.857                  0.462   
10123                0.683                  0.511   
10124     

In [21]:
data.drop(data.columns[[-1, -2]], axis=1, inplace=True)

In [22]:
for column in data.columns:
    print(data[column].value_counts())
    

709920258    1
717171408    1
709372608    1
796336833    1
721433283    1
            ..
720250158    1
709831983    1
720917808    1
719207733    1
708085458    1
Name: CLIENTNUM, Length: 10127, dtype: int64
Existing Customer    8500
Attrited Customer    1627
Name: Attrition_Flag, dtype: int64
44    500
49    495
46    490
45    486
47    479
43    473
48    472
50    452
42    426
51    398
53    387
41    379
52    376
40    361
39    333
54    307
38    303
55    279
56    262
37    260
57    223
36    221
35    184
58    157
59    157
34    146
33    127
60    127
32    106
65    101
61     93
62     93
31     91
26     78
30     70
63     65
29     56
64     43
27     32
28     29
67      4
68      2
66      2
70      1
73      1
Name: Customer_Age, dtype: int64
F    5358
M    4769
Name: Gender, dtype: int64
3    2732
2    2655
1    1838
4    1574
0     904
5     424
Name: Dependent_count, dtype: int64
Graduate         3128
High School      2013
Unknown          1519
Uneducated 

In [23]:
data.set_index('CLIENTNUM', inplace=True)

In [24]:
data['Attrition_Flag'] = data['Attrition_Flag'].map({'Existing Customer': 0, 'Attrited Customer': 1})
data['Gender'] = data['Gender'].map({'F': 0, 'M': 1})
data['Education_Level'] = data['Education_Level'].map({"Doctorate": 0, "Post-Graduate": 1, "College": 2, 
                                                       "Uneducated": 3, "Unknown": 4, "High School": 5,
                                                      "Graduate": 6
                                                      })
data['Marital_Status'] = data['Marital_Status'].map({"Divorced": 0, "Unknown": 1, "Single": 2, 
                                                       "Married": 3
                                                      })
data['Income_Category'] = data['Income_Category'].map({"$120K +": 0, "Unknown": 1, "$60K - $80K": 2, 
                                                       "$80K - $120K": 3, "$40K - $60K": 4, "Less than $40K": 5
                                                      })
data['Card_Category'] = data['Card_Category'].map({"Platinum": 0, "Gold": 1, "Silver": 2, 
                                                       "Blue": 3
                                                      })


In [25]:
data

Attrition_Flag  Customer_Age  Gender  Dependent_count  \
CLIENTNUM                                                          
768805383               0            45       1                3   
818770008               0            49       0                5   
713982108               0            51       1                3   
769911858               0            40       0                4   
709106358               0            40       1                3   
...                   ...           ...     ...              ...   
772366833               0            50       1                2   
710638233               1            41       1                2   
716506083               1            44       0                1   
717406983               1            30       1                2   
714337233               1            43       0                2   

           Education_Level  Marital_Status  Income_Category  Card_Category  \
CLIENTNUM                                                                    
768805383                5               3                2              3   
818770008                6               2                5              3   
713982108                6               3                3              3   
769911858                5               1                5              3   
709106358                3               3                2              3   
...                    ...             ...              ...            ...   
772366833                6               2                4              3   
710638233                4               0                4              3   
716506083                5               3                5              3   
717406983                6               1                4              3   
714337233                6               3                5              2   

           Months_on_book  Total_Relationship_Count  Months_Inactive_12_mon  \
CLIENTNUM                                                                     
768805383              39                         5                       1   
818770008              44                         6                       1   
713982108              36                         4                       1   
769911858              34                         3                       4   
709106358              21                         5                       1   
...                   ...                       ...                     ...   
772366833              40                         3                       2   
710638233              25                         4                       2   
716506083              36                         5                       3   
717406983              36                         4                       3   
714337233              25                         6                       2   

           Contacts_Count_12_mon  Credit_Limit  Total_Revolving_Bal  \
CLIENTNUM                                                             
768805383                      3       12691.0                  777   
818770008                      2        8256.0                  864   
713982108                      0        3418.0                    0   
769911858                      1        3313.0                 2517   
709106358                      0        4716.0                    0   
...                          ...           ...                  ...   
772366833                      3        4003.0                 1851   
710638233                      3        4277.0                 2186   
716506083                      4        5409.0                    0   
717406983                      3        5281.0                    0   
714337233                      4       10388.0                 1961   

           Avg_Open_To_Buy  Total_Amt_Chng_Q4_Q1  Total_Trans_Amt  \
CLIENTNUM                                                           
768805383          11

In [33]:
param = {
    "learning_rate": np.arange(0.01, 0.5, 0.01),
    "n_estimators": range(10, 100, 10)
}

skf = StratifiedKFold(n_splits=5, random_state=17, shuffle=True)

In [30]:
train_x, valid_x, train_y, valid_y = train_test_split(data[data.columns[1:]], data["Attrition_Flag"], test_size=.3,
                                                      random_state=17)

In [34]:
catboost = CatBoostClassifier(random_state = 17)

In [35]:
catboost_grid = GridSearchCV(catboost, param, cv=skf).fit(train_x, train_y)
print("gbc best params", catboost_grid.best_params_)

0:	learn: 0.6866867	total: 5.62ms	remaining: 50.6ms
1:	learn: 0.6800974	total: 9.92ms	remaining: 39.7ms
2:	learn: 0.6739570	total: 14.6ms	remaining: 34ms
3:	learn: 0.6680485	total: 19.1ms	remaining: 28.6ms
4:	learn: 0.6620612	total: 23.8ms	remaining: 23.8ms
5:	learn: 0.6557962	total: 28.5ms	remaining: 19ms
6:	learn: 0.6502086	total: 32.7ms	remaining: 14ms
7:	learn: 0.6445694	total: 37ms	remaining: 9.24ms
8:	learn: 0.6389509	total: 41.3ms	remaining: 4.59ms
9:	learn: 0.6333321	total: 45.9ms	remaining: 0us
0:	learn: 0.6866687	total: 4.29ms	remaining: 38.6ms
1:	learn: 0.6800415	total: 8.86ms	remaining: 35.4ms
2:	learn: 0.6735972	total: 14.7ms	remaining: 34.2ms
3:	learn: 0.6676895	total: 19.4ms	remaining: 29.1ms
4:	learn: 0.6616021	total: 25.9ms	remaining: 25.9ms
5:	learn: 0.6553753	total: 33.3ms	remaining: 22.2ms
6:	learn: 0.6498185	total: 38.7ms	remaining: 16.6ms
7:	learn: 0.6434898	total: 47.8ms	remaining: 11.9ms
8:	learn: 0.6378146	total: 53.2ms	remaining: 5.91ms
9:	learn: 0.6321543	tot

0:	learn: 0.6866687	total: 5.29ms	remaining: 153ms
1:	learn: 0.6800415	total: 11.5ms	remaining: 161ms
2:	learn: 0.6735972	total: 16.4ms	remaining: 147ms
3:	learn: 0.6676895	total: 22.5ms	remaining: 146ms
4:	learn: 0.6616021	total: 30.1ms	remaining: 151ms
5:	learn: 0.6553753	total: 35.2ms	remaining: 141ms
6:	learn: 0.6498185	total: 40.1ms	remaining: 132ms
7:	learn: 0.6434898	total: 45.9ms	remaining: 126ms
8:	learn: 0.6378146	total: 50.8ms	remaining: 119ms
9:	learn: 0.6321543	total: 55.4ms	remaining: 111ms
10:	learn: 0.6264630	total: 62.5ms	remaining: 108ms
11:	learn: 0.6211996	total: 69.6ms	remaining: 104ms
12:	learn: 0.6157904	total: 76.2ms	remaining: 99.6ms
13:	learn: 0.6105658	total: 82.1ms	remaining: 93.8ms
14:	learn: 0.6054581	total: 86.8ms	remaining: 86.8ms
15:	learn: 0.6003062	total: 91.7ms	remaining: 80.3ms
16:	learn: 0.5955524	total: 96.1ms	remaining: 73.5ms
17:	learn: 0.5903621	total: 101ms	remaining: 67.2ms
18:	learn: 0.5854277	total: 106ms	remaining: 61.1ms
19:	learn: 0.5806

12:	learn: 0.6157904	total: 77.3ms	remaining: 161ms
13:	learn: 0.6105658	total: 83.5ms	remaining: 155ms
14:	learn: 0.6054581	total: 89.6ms	remaining: 149ms
15:	learn: 0.6003062	total: 96ms	remaining: 144ms
16:	learn: 0.5955524	total: 102ms	remaining: 138ms
17:	learn: 0.5903621	total: 107ms	remaining: 131ms
18:	learn: 0.5854277	total: 112ms	remaining: 124ms
19:	learn: 0.5806952	total: 117ms	remaining: 117ms
20:	learn: 0.5761536	total: 122ms	remaining: 111ms
21:	learn: 0.5716222	total: 127ms	remaining: 104ms
22:	learn: 0.5672624	total: 132ms	remaining: 97.6ms
23:	learn: 0.5628712	total: 137ms	remaining: 91.4ms
24:	learn: 0.5585450	total: 142ms	remaining: 85.1ms
25:	learn: 0.5542495	total: 150ms	remaining: 81ms
26:	learn: 0.5499343	total: 159ms	remaining: 76.7ms
27:	learn: 0.5454285	total: 171ms	remaining: 73.2ms
28:	learn: 0.5409392	total: 176ms	remaining: 66.6ms
29:	learn: 0.5367219	total: 181ms	remaining: 60.2ms
30:	learn: 0.5325135	total: 185ms	remaining: 53.7ms
31:	learn: 0.5283641	t

31:	learn: 0.5298029	total: 181ms	remaining: 102ms
32:	learn: 0.5259291	total: 188ms	remaining: 97ms
33:	learn: 0.5221217	total: 199ms	remaining: 93.6ms
34:	learn: 0.5184561	total: 206ms	remaining: 88.2ms
35:	learn: 0.5145500	total: 211ms	remaining: 82.2ms
36:	learn: 0.5108473	total: 218ms	remaining: 76.4ms
37:	learn: 0.5072611	total: 226ms	remaining: 71.5ms
38:	learn: 0.5037437	total: 232ms	remaining: 65.5ms
39:	learn: 0.5001402	total: 239ms	remaining: 59.8ms
40:	learn: 0.4966354	total: 247ms	remaining: 54.3ms
41:	learn: 0.4929888	total: 253ms	remaining: 48.3ms
42:	learn: 0.4893037	total: 258ms	remaining: 42.1ms
43:	learn: 0.4860411	total: 264ms	remaining: 36ms
44:	learn: 0.4826012	total: 270ms	remaining: 30ms
45:	learn: 0.4791937	total: 276ms	remaining: 24ms
46:	learn: 0.4758608	total: 283ms	remaining: 18.1ms
47:	learn: 0.4724832	total: 289ms	remaining: 12ms
48:	learn: 0.4690944	total: 294ms	remaining: 6ms
49:	learn: 0.4661401	total: 299ms	remaining: 0us
0:	learn: 0.6866687	total: 5.

41:	learn: 0.4903270	total: 204ms	remaining: 38.9ms
42:	learn: 0.4866796	total: 209ms	remaining: 34.1ms
43:	learn: 0.4833712	total: 215ms	remaining: 29.3ms
44:	learn: 0.4798520	total: 220ms	remaining: 24.5ms
45:	learn: 0.4764221	total: 225ms	remaining: 19.6ms
46:	learn: 0.4730186	total: 229ms	remaining: 14.6ms
47:	learn: 0.4695527	total: 234ms	remaining: 9.76ms
48:	learn: 0.4661049	total: 239ms	remaining: 4.88ms
49:	learn: 0.4629885	total: 243ms	remaining: 0us
0:	learn: 0.6869413	total: 4.85ms	remaining: 238ms
1:	learn: 0.6803758	total: 13.7ms	remaining: 329ms
2:	learn: 0.6738436	total: 22.2ms	remaining: 348ms
3:	learn: 0.6676355	total: 30.6ms	remaining: 352ms
4:	learn: 0.6616656	total: 36.1ms	remaining: 324ms
5:	learn: 0.6556311	total: 41.3ms	remaining: 303ms
6:	learn: 0.6500628	total: 45.9ms	remaining: 282ms
7:	learn: 0.6441584	total: 50.6ms	remaining: 265ms
8:	learn: 0.6386111	total: 56ms	remaining: 255ms
9:	learn: 0.6329525	total: 61.8ms	remaining: 247ms
10:	learn: 0.6271926	total:

...

44:	learn: 0.0575590	total: 185ms	remaining: 144ms
45:	learn: 0.0569122	total: 190ms	remaining: 141ms
46:	learn: 0.0566248	total: 194ms	remaining: 136ms
47:	learn: 0.0564387	total: 199ms	remaining: 132ms
48:	learn: 0.0555500	total: 203ms	remaining: 129ms
49:	learn: 0.0549551	total: 209ms	remaining: 125ms
50:	learn: 0.0542519	total: 214ms	remaining: 121ms
51:	learn: 0.0540276	total: 219ms	remaining: 118ms
52:	learn: 0.0529524	total: 223ms	remaining: 114ms
53:	learn: 0.0514888	total: 228ms	remaining: 110ms
54:	learn: 0.0509522	total: 233ms	remaining: 106ms
55:	learn: 0.0504665	total: 238ms	remaining: 102ms
56:	learn: 0.0494428	total: 244ms	remaining: 98.3ms
57:	learn: 0.0489073	total: 249ms	remaining: 94.5ms
58:	learn: 0.0483680	total: 254ms	remaining: 90.5ms
59:	learn: 0.0474097	total: 259ms	remaining: 86.3ms
60:	learn: 0.0466678	total: 262ms	remaining: 81.7ms
61:	learn: 0.0462828	total: 266ms	remaining: 77.2ms
62:	learn: 0.0457131	total: 270ms	remaining: 72.8ms
63:	learn: 0.0448318	tot

0:	learn: 0.4473053	total: 4.52ms	remaining: 402ms
1:	learn: 0.3388304	total: 9.14ms	remaining: 402ms
2:	learn: 0.2669276	total: 13.2ms	remaining: 383ms
3:	learn: 0.2340505	total: 17.8ms	remaining: 382ms
4:	learn: 0.2089378	total: 22ms	remaining: 375ms
5:	learn: 0.1919049	total: 26.6ms	remaining: 372ms
6:	learn: 0.1716254	total: 31.1ms	remaining: 369ms
7:	learn: 0.1613853	total: 35.9ms	remaining: 368ms
8:	learn: 0.1474561	total: 40.3ms	remaining: 362ms
9:	learn: 0.1380853	total: 43.8ms	remaining: 350ms
10:	learn: 0.1326186	total: 47.5ms	remaining: 341ms
11:	learn: 0.1220142	total: 50.9ms	remaining: 331ms
12:	learn: 0.1199036	total: 54.5ms	remaining: 323ms
13:	learn: 0.1147979	total: 58.2ms	remaining: 316ms
14:	learn: 0.1063674	total: 61.9ms	remaining: 310ms
15:	learn: 0.1047792	total: 65.5ms	remaining: 303ms
16:	learn: 0.0991380	total: 69.1ms	remaining: 297ms
17:	learn: 0.0952632	total: 73ms	remaining: 292ms
18:	learn: 0.0918687	total: 76.5ms	remaining: 286ms
19:	learn: 0.0902237	total

0:	learn: 0.4547502	total: 3.87ms	remaining: 345ms
1:	learn: 0.3384077	total: 7.31ms	remaining: 322ms
2:	learn: 0.2658928	total: 10.8ms	remaining: 314ms
3:	learn: 0.2387362	total: 14.6ms	remaining: 313ms
4:	learn: 0.2015251	total: 18.6ms	remaining: 316ms
5:	learn: 0.1779723	total: 22.1ms	remaining: 309ms
6:	learn: 0.1588947	total: 25.4ms	remaining: 301ms
7:	learn: 0.1490882	total: 29.1ms	remaining: 298ms
8:	learn: 0.1406571	total: 32.7ms	remaining: 294ms
9:	learn: 0.1320703	total: 36ms	remaining: 288ms
10:	learn: 0.1267923	total: 39.3ms	remaining: 282ms
11:	learn: 0.1216209	total: 42.6ms	remaining: 277ms
12:	learn: 0.1142142	total: 45.8ms	remaining: 271ms
13:	learn: 0.1098218	total: 49.1ms	remaining: 267ms
14:	learn: 0.1074138	total: 52.5ms	remaining: 262ms
15:	learn: 0.1036018	total: 56.3ms	remaining: 260ms
16:	learn: 0.1000861	total: 60ms	remaining: 257ms
17:	learn: 0.0969883	total: 63.7ms	remaining: 255ms
18:	learn: 0.0928608	total: 67.2ms	remaining: 251ms
19:	learn: 0.0909447	total

0:	learn: 0.4565863	total: 5.73ms	remaining: 510ms
1:	learn: 0.3486885	total: 9.32ms	remaining: 410ms
2:	learn: 0.2696525	total: 12.8ms	remaining: 373ms
3:	learn: 0.2400822	total: 16.1ms	remaining: 347ms
4:	learn: 0.2103761	total: 19.4ms	remaining: 329ms
5:	learn: 0.1830668	total: 22.6ms	remaining: 316ms
6:	learn: 0.1673277	total: 25.8ms	remaining: 305ms
7:	learn: 0.1583766	total: 28.9ms	remaining: 296ms
8:	learn: 0.1513221	total: 32.5ms	remaining: 293ms
9:	learn: 0.1436350	total: 36.1ms	remaining: 289ms
10:	learn: 0.1356447	total: 39.1ms	remaining: 281ms
11:	learn: 0.1266338	total: 42.6ms	remaining: 277ms
12:	learn: 0.1218181	total: 46ms	remaining: 272ms
13:	learn: 0.1171554	total: 49.9ms	remaining: 271ms
14:	learn: 0.1127298	total: 54ms	remaining: 270ms
15:	learn: 0.1067962	total: 58ms	remaining: 268ms
16:	learn: 0.1024474	total: 61.6ms	remaining: 265ms
17:	learn: 0.0978629	total: 64.9ms	remaining: 260ms
18:	learn: 0.0944523	total: 68.1ms	remaining: 254ms
19:	learn: 0.0923073	total: 

gbc best params {'learning_rate': 0.41000000000000003, 'n_estimators': 90}


In [36]:
from sklearn.metrics import accuracy_score
print(f'Accuracy: {accuracy_score(valid_y, catboost_grid.predict(valid_x))}')

Accuracy: 0.9667653833497861


In [37]:
catboost = CatBoostClassifier(learning_rate= 0.41000000000000003, n_estimators = 90, random_state = 17)

In [38]:
catboost.fit(train_x, train_y, plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 0.4755202	total: 31.9ms	remaining: 2.84s
1:	learn: 0.3669907	total: 54.7ms	remaining: 2.41s
2:	learn: 0.2889228	total: 65.4ms	remaining: 1.9s
3:	learn: 0.2425318	total: 70.9ms	remaining: 1.52s
4:	learn: 0.2122350	total: 76.1ms	remaining: 1.29s
5:	learn: 0.1933104	total: 82.5ms	remaining: 1.16s
6:	learn: 0.1764580	total: 87.3ms	remaining: 1.03s
7:	learn: 0.1678276	total: 91.6ms	remaining: 939ms
8:	learn: 0.1549111	total: 97.5ms	remaining: 877ms
9:	learn: 0.1462247	total: 102ms	remaining: 816ms
10:	learn: 0.1390271	total: 106ms	remaining: 764ms
11:	learn: 0.1337031	total: 114ms	remaining: 738ms
12:	learn: 0.1288913	total: 120ms	remaining: 708ms
13:	learn: 0.1243367	total: 125ms	remaining: 681ms
14:	learn: 0.1194277	total: 130ms	remaining: 652ms
15:	learn: 0.1156771	total: 135ms	remaining: 626ms
16:	learn: 0.1090447	total: 141ms	remaining: 603ms
17:	learn: 0.1046595	total: 145ms	remaining: 582ms
18:	learn: 0.1009845	total: 151ms	remaining: 563ms
19:	learn: 0.0965283	total: 156ms

In [39]:
print(f'Accuracy: {accuracy_score(valid_y, catboost.predict(valid_x))}')

Accuracy: 0.9667653833497861
